In [1]:
# Import Libraries
import pandas as pd
import geopandas as gpd
import lxml
import os
import glob
import time
import datetime
import json


In [2]:
# Set Output Folder
output_folder = os.path.abspath("output")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)


In [3]:
# Import data folders
project_data_folder = os.path.abspath("Data")
DISE_data_folder = os.path.join(project_data_folder, "DISE")
agg_data_folder = os.path.join(DISE_data_folder, "Aggregated")
data_folder = agg_data_folder
folders = os.listdir(data_folder)
## Make Noise
print("data found for these themes:")
i = 0
for folder in folders:
    print(i,") ",folder)
    i+=1

data found for these themes:
0 )  DISE_Basic_Data
1 )  DISE_Facility_Data
2 )  DISE_General_Data
3 )  DISE_Total
4 )  DISE_Teachers
5 )  DISE_DisabledEnrolment_Data
6 )  DISE_OBCEnrolment_Data
7 )  DISE_Repeaters_Data
8 )  DISE_RTE_Data
9 )  DISE_ST
10 )  DISE_SC


In [4]:
# Data Cleaning function
def clean_columns(columns):
    # Capitalize everything
    columns = [x.upper() for x in columns]
    # General Columns
    columns = [x.replace('SCHOOL_CODE', 'SCHCD') for x in columns]
    columns = [x.replace('ACYEAR', 'AC_YEAR') for x in columns]
    # Theme-DISE_Basic_Data
    columns = [x.replace('DISTRICT_NAME', 'DISTNAME') for x in columns]
    # Theme-DISE_Facility_Data
    columns = [x.replace('BUILDING_STATUS', 'BLDSTATUS') for x in columns]
    columns = [x.replace('TOT_CLROOMS', 'CLROOMS') for x in columns]
    columns = [x.replace('CLASSROOMS_IN_GOOD_CONDITION', 'CLGOOD') for x in columns]
    columns = [x.replace('CLASSROOMS_REQUIRE_MAJOR_REPAIR', 'CLMAJOR') for x in columns]
    columns = [x.replace('CLASSROOMS_REQUIRE_MINOR_REPAIR', 'CLMINOR') for x in columns]
    columns = [x.replace('TOILET_BOYS', 'TOILETB') for x in columns]
    columns = [x.replace('TOILET_GIRLS', 'TOILET_G') for x in columns]
    columns = [x.replace('NO_OF_COMPUTERS', 'COMPUTER') for x in columns]
    columns = [x.replace('KITCHEN_DEVICES_GRANT', 'KITDEVGRANT_YN') for x in columns]    
    columns = [x.replace('STATUS_OF_MDM', 'MEALSINSCH') for x in columns]  
    columns = [x.replace('COMPUTER_AIDED_LEARNIN_LAB', 'CAL_YN') for x in columns]  
    columns = [x.replace('SEPARATE_ROOM_FOR_HEADMASTER', 'HMROOM_YN') for x in columns]
    columns = [x.replace('ELECTRICITY', 'ELECTRIC_YN') for x in columns]
    columns = [x.replace('BOUNDARY_WALL', 'BNDRYWALL') for x in columns]
    columns = [x.replace('LIBRARY_YN', 'LIBRARY_YN') for x in columns]
    columns = [x.replace('PLAYGROUND', 'PGROUND_YN') for x in columns]
    columns = [x.replace('BOOKS_IN_LIBRARY', 'BOOKINLIB') for x in columns]
    columns = [x.replace('DRINKING_WATER', 'WATER') for x in columns]
    columns = [x.replace('MEDICAL_CHECKUP', 'MEDCHK_YN') for x in columns]
    columns = [x.replace('RAMPS', 'RAMPS_YN') for x in columns]
    columns = [x.replace('MALE_TCH', 'TCH_MALE') for x in columns]
    columns = [x.replace('FEMALE_TCH', 'TCH_FEMALE') for x in columns]
    columns = [x.replace('NORESP_TCH', 'TCH_NR') for x in columns]
    columns = [x.replace('HEAD_TEACHER', 'HEADTCH') for x in columns]
    columns = [x.replace('GRADUATE_TEACHERS', 'GRADABOVE') for x in columns]
    columns = [x.replace('TCH_WITH_PROFESSIONAL_QUALIFICATION', 'TCHWITHPROF') for x in columns]
    columns = [x.replace('DAYS_INVOLVED_IN_NON_TCH_ASSGN', 'DAYSINVLD') for x in columns]
    columns = [x.replace('TEACHERS_INVOLVED_IN_NON_TCH_ASSGN', 'TCHINVLD') for x in columns]
    # Theme-DISE_General_Data
    columns = [x.replace('RURAL_URBAN', 'RURURB') for x in columns]
    columns = [x.replace('MEDIUM1', 'MEDINSTR1') for x in columns]
    columns = [x.replace('MEDIUM2', 'MEDINSTR2') for x in columns]
    columns = [x.replace('MEDIUM3', 'MEDINSTR3') for x in columns]
    columns = [x.replace('MEDIUM4', 'MEDINSTR4') for x in columns]
    columns = [x.replace('DISTANCE_BRC', 'DISTHQ') for x in columns]
    columns = [x.replace('DISTANCE_CRC', 'DISTCRC') for x in columns]
    columns = [x.replace('YEUR_ESTD', 'ESTDYEAR') for x in columns]
    columns = [x.replace('PRE_PRY_YN', 'PPSEC_YN') for x in columns]
    columns = [x.replace('RESIDENTIAL_SCH_YN', 'SCHRES_YN') for x in columns]
    columns = [x.replace('SCH_MANAGEMENT', 'SCHMGT') for x in columns]
    columns = [x.replace('LOWEST_CLASS', 'LOWCLASS') for x in columns]
    columns = [x.replace('HIGHEST_CLASS', 'HIGHCLASS') for x in columns]
    columns = [x.replace('SCH_CATEGORY', 'SCHCAT') for x in columns]
    columns = [x.replace('PRE_PRY_STUDENTS', 'PPSTUDENT') for x in columns]
    columns = [x.replace('SCHOOL_TYPE', 'SCHTYPE') for x in columns]
    columns = [x.replace('SHIFT_SCHOOL_YN', 'SCHSHI_YN') for x in columns]
    columns = [x.replace('NO_OF_WORKING_DAYS', 'WORKDAYS') for x in columns]
    columns = [x.replace('NO_OF_ACAD_INSPECTION', 'NOINSPECT') for x in columns]
    columns = [x.replace('RESIDENTIAL_SCH_TYPE', 'RESITYPE') for x in columns]
    columns = [x.replace('PRE_PRY_TEACHERS', 'PPTEACHER') for x in columns]
    columns = [x.replace('VISITS_BY_BRC', 'VISITSBRC') for x in columns]
    columns = [x.replace('VISITS_BY_CRC', 'VISITSCRC') for x in columns]
    columns = [x.replace('SCHOOL_DEV_GRANT_RECD', 'CONTI_R') for x in columns]
    columns = [x.replace('SCHOOL_DEV_GRANT_EXPND', 'CONTI_E') for x in columns]
    columns = [x.replace('TLM_GRANT_RECD', 'TLM_R') for x in columns]
    columns = [x.replace('FUNDS_FROM_STUDENTS_RECD', 'FUNDS_R') for x in columns]
    columns = [x.replace('FUNDS_FROM_STUDENTS_EXPND', 'FUNDS_E') for x in columns]
    # Theme- DISE_Total
    columns = [x.replace('CLASS1_TOTAL_ENR_BOYS', 'C1_TOTB') for x in columns]
    columns = [x.replace('CLASS1_TOTAL_ENR_GIRLS', 'C1_TOTG') for x in columns]
    columns = [x.replace('CLASS2_TOTAL_ENR_BOYS', 'C2_TOTB') for x in columns]
    columns = [x.replace('CLASS2_TOTAL_ENR_GIRLS', 'C2_TOTG') for x in columns]
    columns = [x.replace('CLASS3_TOTAL_ENR_BOYS', 'C3_TOTB') for x in columns]
    columns = [x.replace('CLASS3_TOTAL_ENR_GIRLS', 'C3_TOTG') for x in columns]
    columns = [x.replace('CLASS4_TOTAL_ENR_BOYS', 'C4_TOTB') for x in columns]
    columns = [x.replace('CLASS4_TOTAL_ENR_GIRLS', 'C4_TOTG') for x in columns]
    columns = [x.replace('CLASS5_TOTAL_ENR_BOYS', 'C5_TOTB') for x in columns]
    columns = [x.replace('CLASS5_TOTAL_ENR_GIRLS', 'C5_TOTG') for x in columns]
    columns = [x.replace('CLASS6_TOTAL_ENR_BOYS', 'C6_TOTB') for x in columns]
    columns = [x.replace('CLASS6_TOTAL_ENR_GIRLS', 'C6_TOTG') for x in columns]
    columns = [x.replace('CLASS7_TOTAL_ENR_BOYS', 'C7_TOTB') for x in columns]
    columns = [x.replace('CLASS7_TOTAL_ENR_GIRLS', 'C7_TOTG') for x in columns]
    columns = [x.replace('CLASS8_TOTAL_ENR_BOYS', 'C8_TOTB') for x in columns]
    columns = [x.replace('CLASS8_TOTAL_ENR_GIRLS', 'C8_TOTG') for x in columns]
    columns = [x.replace('CLASS9_TOTAL_ENR_BOYS', 'C9_TOTB') for x in columns]
    columns = [x.replace('CLASS9_TOTAL_ENR_GIRLS', 'C9_TOTG') for x in columns]
    columns = [x.replace('CLASS10_TOTAL_ENR_BOYS', 'C10_TOTB') for x in columns]
    columns = [x.replace('CLASS10_TOTAL_ENR_GIRLS', 'C10_TOTG') for x in columns]
    columns = [x.replace('CLASS11_TOTAL_ENR_BOYS', 'C11_TOTB') for x in columns]
    columns = [x.replace('CLASS11_TOTAL_ENR_GIRLS', 'C11_TOTG') for x in columns]
    columns = [x.replace('CLASS12_TOTAL_ENR_BOYS', 'C12_TOTB') for x in columns]
    columns = [x.replace('CLASS12_TOTAL_ENR_GIRLS', 'C12_TOTG') for x in columns]
    columns = [x.replace('C5_APPEARED_BOYS', 'APPRB5') for x in columns]
    columns = [x.replace('C5_APPEARED_GIRLS', 'APPRG5') for x in columns]
    columns = [x.replace('C7_APPEARED_BOYS', 'APPRB8') for x in columns]
    columns = [x.replace('C7_APPEARED_GIRLS', 'APPRG8') for x in columns]
    columns = [x.replace('C5_PASSED_BOYS', 'PASSB5') for x in columns]
    columns = [x.replace('C5_PASSED_GIRLS', 'PASSG5') for x in columns]
    columns = [x.replace('C7_PASSED_BOYS', 'PASSB8') for x in columns]
    columns = [x.replace('C7_PASSED_GIRLS', 'PASSG8') for x in columns]
    columns = [x.replace('C5_PASSED_WITH_MORE_THAN_60_BOYS', 'P60B5') for x in columns]
    columns = [x.replace('C5_PASSED_WITH_MORE_THAN_60_GIRLS', 'P60G5') for x in columns]
    columns = [x.replace('C7_PASSED_WITH_MORE_THAN_60_BOYS', 'P60B8') for x in columns]
    columns = [x.replace('C7_PASSED_WITH_MORE_THAN_60_GIRLS', 'P60G8') for x in columns]
    # Theme-DISE_Teachers
    ## Capitalize only
    # Theme-DISE_DisabledEnrolment_Data
    columns = [x.replace('DISABLED_C1_BOYS', 'C1_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C2_BOYS', 'C2_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C3_BOYS', 'C3_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C4_BOYS', 'C4_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C5_BOYS', 'C5_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C6_BOYS', 'C6_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C7_BOYS', 'C7_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C8_BOYS', 'C8_DIS_B') for x in columns]
    columns = [x.replace('DISABLED_C1_GIRLS', 'C1_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C2_GIRLS', 'C2_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C3_GIRLS', 'C3_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C4_GIRLS', 'C4_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C5_GIRLS', 'C5_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C6_GIRLS', 'C6_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C7_GIRLS', 'C7_DIS_G') for x in columns]
    columns = [x.replace('DISABLED_C8_GIRLS', 'C8_DIS_G') for x in columns]
    # Theme-DISE_OBCEnrolment_Data
    columns = [x.replace('CLASS1_OBC_ENR_BOYS', 'C1_OB') for x in columns]
    columns = [x.replace('CLASS2_OBC_ENR_BOYS', 'C2_OB') for x in columns]
    columns = [x.replace('CLASS3_OBC_ENR_BOYS', 'C3_OB') for x in columns]
    columns = [x.replace('CLASS4_OBC_ENR_BOYS', 'C4_OB') for x in columns]
    columns = [x.replace('CLASS5_OBC_ENR_BOYS', 'C5_OB') for x in columns]
    columns = [x.replace('CLASS6_OBC_ENR_BOYS', 'C6_OB') for x in columns]
    columns = [x.replace('CLASS7_OBC_ENR_BOYS', 'C7_OB') for x in columns]
    columns = [x.replace('CLASS8_OBC_ENR_BOYS', 'C8_OB') for x in columns]
    columns = [x.replace('CLASS1_OBC_ENR_GIRLS', 'C1_OG') for x in columns]
    columns = [x.replace('CLASS2_OBC_ENR_GIRLS', 'C2_OG') for x in columns]
    columns = [x.replace('CLASS3_OBC_ENR_GIRLS', 'C3_OG') for x in columns]
    columns = [x.replace('CLASS4_OBC_ENR_GIRLS', 'C4_OG') for x in columns]
    columns = [x.replace('CLASS5_OBC_ENR_GIRLS', 'C5_OG') for x in columns]
    columns = [x.replace('CLASS6_OBC_ENR_GIRLS', 'C6_OG') for x in columns]
    columns = [x.replace('CLASS7_OBC_ENR_GIRLS', 'C7_OG') for x in columns]
    columns = [x.replace('CLASS8_OBC_ENR_GIRLS', 'C8_OG') for x in columns]
    # Theme-DISE_Repeaters_Data
    columns = [x.replace('REPEATERS_C1_BOYS', 'FAIL1B') for x in columns]
    columns = [x.replace('REPEATERS_C2_BOYS', 'FAIL2B') for x in columns]
    columns = [x.replace('REPEATERS_C3_BOYS', 'FAIL3B') for x in columns]
    columns = [x.replace('REPEATERS_C4_BOYS', 'FAIL4B') for x in columns]
    columns = [x.replace('REPEATERS_C5_BOYS', 'FAIL5B') for x in columns]
    columns = [x.replace('REPEATERS_C6_BOYS', 'FAIL6B') for x in columns]
    columns = [x.replace('REPEATERS_C7_BOYS', 'FAIL7B') for x in columns]
    columns = [x.replace('REPEATERS_C8_BOYS', 'FAIL8B') for x in columns]
    columns = [x.replace('REPEATERS_C1_GIRLS', 'FAIL1G') for x in columns]
    columns = [x.replace('REPEATERS_C2_GIRLS', 'FAIL2G') for x in columns]
    columns = [x.replace('REPEATERS_C3_GIRLS', 'FAIL3G') for x in columns]
    columns = [x.replace('REPEATERS_C4_GIRLS', 'FAIL4G') for x in columns]
    columns = [x.replace('REPEATERS_C5_GIRLS', 'FAIL5G') for x in columns]
    columns = [x.replace('REPEATERS_C6_GIRLS', 'FAIL6G') for x in columns]
    columns = [x.replace('REPEATERS_C7_GIRLS', 'FAIL7G') for x in columns]
    columns = [x.replace('REPEATERS_C8_GIRLS', 'FAIL8G') for x in columns]
    # Theme-DISE_RTE_Data
    columns = [x.replace('WORKING_DAYS_PRIMARY', 'WORKDAYS_PR') for x in columns]
    columns = [x.replace('WORKING_DAYS_UPRIMARY', 'WORKDAYS_UPR') for x in columns]
    columns = [x.replace('SCHOOOL_HOURS_CHILDREN_PRI', 'SCHHRSCHILD_PR') for x in columns]
    columns = [x.replace('SCHOOL_HOURS_CHILDREN_UPRI', 'SCHHRSCHILD_UPR') for x in columns]
    columns = [x.replace('SCHOOL_HOURS_TCH_P', 'SCHHRSTCH_PR') for x in columns]
    columns = [x.replace('SCHOOL_HOURS_TCH_UPR', 'SCHHRSTCH_UPR') for x in columns]
    columns = [x.replace('APPROACHABLE_BY_ALL_WEATHER_ROAD', 'APPROACHBYROAD') for x in columns]
    columns = [x.replace('CCE_IMPLEMENTED', 'CCE_YN') for x in columns]
    columns = [x.replace('PEOPLE_CUMILATIVERE_RECORD_MAINTAINED', 'PCR_MAINTAINED') for x in columns]
    columns = [x.replace('PCR_SHARED_WITH_PARENTS', 'PCR_SHARED') for x in columns]
    columns = [x.replace('CHILDREN_FROM_WEAKER_SECTION_APPLIED', 'WSEC25P_APPLIED') for x in columns]
    columns = [x.replace('CHILDREN_FROM_WEAKER_SECTION_ENROLLED', 'WSEC25P_ENROLLED') for x in columns]
    columns = [x.replace('AID_RECEIVED', 'AIDRECD') for x in columns]
    columns = [x.replace('CHILREN_ADMITTED_FOR_FREE_EDUCATION', 'STUADMITTED') for x in columns]
    columns = [x.replace('SMC_CONSTITUTED', 'SMC_YN') for x in columns]
    columns = [x.replace('SMC_MEMBERS_MALE', 'SMCMEM_M') for x in columns]
    columns = [x.replace('SMC_MEMBERS_FEMALE', 'SMCMEM_F') for x in columns]
    columns = [x.replace('SMC_MEMBERS_PARENTS_MALE', 'SMSPARENTS_M') for x in columns]
    columns = [x.replace('SMC_MEMBERS_PARENTS_FEMALE', 'SMSPARENTS_F') for x in columns]
    columns = [x.replace('SMC_MEMBERS_LOCAL_AUTHORITY_MALE', 'SMCNOMLOCAL_M') for x in columns]
    columns = [x.replace('SMC_MEMBERS_LOCAL_AUTHORITY_FEMALE', 'SMCNOMLOCAL_F') for x in columns]
    columns = [x.replace('SMC_MEETINGS_HELD', 'SMCMEETINGS') for x in columns]
    columns = [x.replace('SCHOOL_DEVELOPMENTPLAN_PREPARED', 'SMCSDP_YN') for x in columns]
    columns = [x.replace('SMC_CHILDREN_RECORD_MAINTAINED', 'WORKDAYS_PR') for x in columns]
    columns = [x.replace('CHLD_ENROLLED_FOR_SP_TRAINING_CURRENT_YEAR_B', 'SPLTRG_CY_ENROLLED_B') for x in columns]
    columns = [x.replace('CHLD_ENROLLED_FOR_SP_TRAINING_CURRENT_YEAR_G', 'SPLTRG_CY_ENROLLED_G') for x in columns]
    columns = [x.replace('SPL_TRAINING_PROVIDED_CURRENT_YEAR_B', 'SPLTRG_CY_PROVIDED_B') for x in columns]
    columns = [x.replace('SPL_TRAINING_PROVIDED_CURRENT_YEAR_G', 'SPLTRG_CY_PROVIDED_G') for x in columns]
    columns = [x.replace('SPL_TRAINING_ENROLLED_PREVIOUS_YEAR_B', 'SPLTRG_PY_ENROLLED_B') for x in columns]
    columns = [x.replace('SPL_TRAINING_ENROLLED_PREVIOUS_YEAR_G', 'SPLTRG_PY_ENROLLED_G') for x in columns]
    columns = [x.replace('SPL_TRAINING_PROVIDED_PREVIOUS_YEAR_B', 'SPLTRG_PY_PROVIDED_B') for x in columns]
    columns = [x.replace('SPL_TRAINING_PROVIDED_PREVIOUS_YEAR_G', 'SPLTRG_PY_PROVIDED_G') for x in columns]
    columns = [x.replace('SPL_TRAINING_CONDUCTED_BY', 'SPLTRG_BY') for x in columns]
    columns = [x.replace('SPL_TRAINING_PLACE', 'SPLTRG_PLACE') for x in columns]
    columns = [x.replace('SPL_TRAINING_TYPE', 'SPLTRG_TYPE') for x in columns]
    columns = [x.replace('TCH_OR_EVS_FOR_SPL_TRAINING', 'SPLTRG_TOTEV') for x in columns]
    columns = [x.replace('SPL_TRAINING_MATERIAL', 'SPLTRG_MATERIAL_YN') for x in columns]
    columns = [x.replace('TEXTBOOK_RECEIVED', 'TXTBKRECD_YN') for x in columns]
    columns = [x.replace('TEXT_BOOK_RECEIVED_MONTH', 'TXTBKMNTH') for x in columns]
    columns = [x.replace('TEXT_BOOK_RECEIVED_YEAR', 'TXTBKYEAR') for x in columns]
    columns = [x.replace('ACADEMIC_SESSION_START_IN', 'ACSTARTMNTH') for x in columns]
    columns = [x.replace('MDM_STATUS', 'MEALSINSCH') for x in columns]
    columns = [x.replace('KITCHENSHED_STATUS', 'KITSHED') for x in columns]
    columns = [x.replace('MDM_SOURCE', 'MDM_MAINTAINER') for x in columns]
    columns = [x.replace('DAYS_MEALS_SERVED', 'DAYS_WITHFOOD') for x in columns]
    columns = [x.replace('MEALS_SERVED_PREV_YR', 'MEALSERVED') for x in columns]
    columns = [x.replace('STUDENTS_OPTED_MDM_B', 'BENEFITTED_BOYS') for x in columns]
    columns = [x.replace('STDENTS_OPTED_MDM_G', 'BENEFITTED_GIRLS') for x in columns]
    columns = [x.replace('KITCHEN_DEVAICES_GRANT', 'KITDEVGRANT_YN') for x in columns]
    columns = [x.replace('INSPECTIONS_BY_SO', 'INSPECT_SO') for x in columns]
    columns = [x.replace('INSPECTIONS_BY_CM', 'INSPECT_CM') for x in columns]
    # Theme-DISE_ST
    columns = [x.replace('CLASS1_ST_ENR_BOYS', 'T1_CB') for x in columns]
    columns = [x.replace('CLASS2_ST_ENR_BOYS', 'T2_CB') for x in columns]
    columns = [x.replace('CLASS3_ST_ENR_BOYS', 'T3_CB') for x in columns]
    columns = [x.replace('CLASS4_ST_ENR_BOYS', 'T4_CB') for x in columns]
    columns = [x.replace('CLASS5_ST_ENR_BOYS', 'T5_CB') for x in columns]
    columns = [x.replace('CLASS6_ST_ENR_BOYS', 'T6_CB') for x in columns]
    columns = [x.replace('CLASS7_ST_ENR_BOYS', 'T7_CB') for x in columns]
    columns = [x.replace('CLASS8_ST_ENR_BOYS', 'T8_CB') for x in columns]
    columns = [x.replace('CLASS1_ST_ENR_GIRLS', 'T1_CG') for x in columns]
    columns = [x.replace('CLASS2_ST_ENR_GIRLS', 'T2_CG') for x in columns]
    columns = [x.replace('CLASS3_ST_ENR_GIRLS', 'T3_CG') for x in columns]
    columns = [x.replace('CLASS4_ST_ENR_GIRLS', 'T4_CG') for x in columns]
    columns = [x.replace('CLASS5_ST_ENR_GIRLS', 'T5_CG') for x in columns]
    columns = [x.replace('CLASS6_ST_ENR_GIRLS', 'T6_CG') for x in columns]
    columns = [x.replace('CLASS7_ST_ENR_GIRLS', 'T7_CG') for x in columns]
    columns = [x.replace('CLASS8_ST_ENR_GIRLS', 'T8_CG') for x in columns]
    # Theme-DISE_SC
    columns = [x.replace('CLASS1_SC_ENR_BOYS', 'C1_CB') for x in columns]
    columns = [x.replace('CLASS2_SC_ENR_BOYS', 'C2_CB') for x in columns]
    columns = [x.replace('CLASS3_SC_ENR_BOYS', 'C3_CB') for x in columns]
    columns = [x.replace('CLASS4_SC_ENR_BOYS', 'C4_CB') for x in columns]
    columns = [x.replace('CLASS5_SC_ENR_BOYS', 'C5_CB') for x in columns]
    columns = [x.replace('CLASS6_SC_ENR_BOYS', 'C6_CB') for x in columns]
    columns = [x.replace('CLASS7_SC_ENR_BOYS', 'C7_CB') for x in columns]
    columns = [x.replace('CLASS8_SC_ENR_BOYS', 'C8_CB') for x in columns]
    columns = [x.replace('CLASS1_SC_ENR_GIRLS', 'C1_CG') for x in columns]
    columns = [x.replace('CLASS2_SC_ENR_GIRLS', 'C2_CG') for x in columns]
    columns = [x.replace('CLASS3_SC_ENR_GIRLS', 'C3_CG') for x in columns]
    columns = [x.replace('CLASS4_SC_ENR_GIRLS', 'C4_CG') for x in columns]
    columns = [x.replace('CLASS5_SC_ENR_GIRLS', 'C5_CG') for x in columns]
    columns = [x.replace('CLASS6_SC_ENR_GIRLS', 'C6_CG') for x in columns]
    columns = [x.replace('CLASS7_SC_ENR_GIRLS', 'C7_CG') for x in columns]
    columns = [x.replace('CLASS8_SC_ENR_GIRLS', 'C8_CG') for x in columns]
    return columns

In [5]:
# Skip folders
x = 8
folders = folders[x:]
#folders = folders[x:x+1]
# Merge data
for folder in folders:
    print("--Preparing Data for this theme", folder)
    # get all the files in folder
    curr_folder = os.path.join(data_folder, folder)
    files = os.listdir(curr_folder)
    # Filter all excel files and create absolute paths
    files = [a for a in files if ( a.split(".")[-1] == "xlsx" or a.split(".")[-1] == "xls" ) ]
    files = [ os.path.join(curr_folder, a) for a in files]
    # Get name of data theme
    xl = pd.ExcelFile(files[0])
    sheet_name = xl.sheet_names[0]
    # Flush memory with new variables
    df = None
    columns = None
    df_list = []
    # Loop over all files and aggregate
    for file in files:
        try:
            print("----Reading data from file", file)
            xl = pd.ExcelFile(file)
            df1 = xl.parse(sheet_name)
            #print(df1.columns)
            # Clean Columns
            df1.columns = clean_columns(df1.columns)
            # Append Dataframe to List
            df_list.append(df1)
        except Exception as e:
            print("----Error Reading data | file ", file, " | Error: ", e)
    # Merge all files
    df = pd.concat(df_list)
    # Export file to ouput directry
    out_file = os.path.join(output_folder, sheet_name + '.csv')
    df.to_csv(out_file, encoding='utf-8', index=False)
    print("----Saving data to file", out_file)

--Preparing Data for this theme DISE_RTE_Data
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 09-31-53.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 15-03-50.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 09-10-33.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 12-47-06.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 04-47-54.xlsx
----Reading data from file /home/sandyjones/

----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_17-03-2018 14-16-00.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 08-58-25.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 08-27-33.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 01-08-19.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 13-10-52.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode High

----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 06-52-37.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 15-06-04.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 04-50-34.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_21-03-2018 06-37-49.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 08-54-20.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode High

----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_16-03-2018 01-41-31.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 02-55-18.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 08-40-02.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 11-58-31.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_14-03-2018 03-23-14.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode High

----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 16-16-53.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 15-29-23.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 12-42-52.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 23-53-53.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode Higher education Data/Data/DISE/Aggregated/DISE_RTE_Data/DISE_RTE_Data_15-03-2018 10-13-38.xlsx
----Reading data from file /home/sandyjones/Desktop/do/Sourav_Sarkar/Task 5 - Geocode High

ValueError: Plan shapes are not aligned